In [2]:
import numpy as np
import pandas as pd
import plotly.express as px
import plotly.graph_objects as go
import glob2 as glob
import os

In [10]:
# load nucleus point clouds 
root = "/media/nick/hdd02/Cole Trapnell's Lab Dropbox/Nick Lammers/Nick/pecfin_dynamics/"
fluo_channel = "tbx5a-StayGold_mean_nn"
experiment_date = "20240223" # ["20240424", "20240425"]
data_root = os.path.join(root, "built_data", "nucleus_data", "point_clouds", experiment_date)

# specify which well
well_id = 12
stub = experiment_date + f"_well{well_id:04}*"

# get list of datasets
df_list = sorted(glob.glob(os.path.join(data_root, stub)))
print(df_list)

["/media/nick/hdd02/Cole Trapnell's Lab Dropbox/Nick Lammers/Nick/pecfin_dynamics/built_data/nucleus_data/point_clouds/20240223/20240223_well0012_time0000_points.csv", "/media/nick/hdd02/Cole Trapnell's Lab Dropbox/Nick Lammers/Nick/pecfin_dynamics/built_data/nucleus_data/point_clouds/20240223/20240223_well0012_time0001_points.csv", "/media/nick/hdd02/Cole Trapnell's Lab Dropbox/Nick Lammers/Nick/pecfin_dynamics/built_data/nucleus_data/point_clouds/20240223/20240223_well0012_time0002_points.csv", "/media/nick/hdd02/Cole Trapnell's Lab Dropbox/Nick Lammers/Nick/pecfin_dynamics/built_data/nucleus_data/point_clouds/20240223/20240223_well0012_time0003_points.csv", "/media/nick/hdd02/Cole Trapnell's Lab Dropbox/Nick Lammers/Nick/pecfin_dynamics/built_data/nucleus_data/point_clouds/20240223/20240223_well0012_time0004_points.csv", "/media/nick/hdd02/Cole Trapnell's Lab Dropbox/Nick Lammers/Nick/pecfin_dynamics/built_data/nucleus_data/point_clouds/20240223/20240223_well0012_time0005_points.csv

In [55]:
from probreg import cpd
import time
# tf_param = bcpd.registration_bcpd(source_pcd, target_pcd)
# result_pcd = copy.deepcopy(source_pcd)
# result_pcd.points = tf_param.transform(result_pcd.points)

start_t = 50
point_df0 = pd.read_csv(df_list[start_t])
points0 = point_df0.loc[:, ["Z", "Y", "X"]].to_numpy()
point_df1 = pd.read_csv(df_list[start_t+10])
points1 = point_df1.loc[:, ["Z", "Y", "X"]].to_numpy()
point_df2 = pd.read_csv(df_list[start_t+10])
points2 = point_df1.loc[:, ["Z", "Y", "X"]].to_numpy()

# source_pt = np.asarray(points0, dtype=np.float32)
# target_pt = np.asarray(points1, dtype=np.float32)
start = time.time()
print("performing first registration...")
acpd01 = cpd.NonRigidCPD(points0, use_cuda=False)
tf_param01, _, _ = acpd01.registration(points1)
result01 = tf_param01.transform(points0)
start2 = time.time()

print(start2-start)
print("performing second registration...")
acpd12 = cpd.NonRigidCPD(points1, use_cuda=False)
tf_param12, _, _ = acpd.registration(points2)
result12 = tf_param.transform(points1)

print(time.time() - start2)

performing first registration...
36.85590982437134
performing second registration...
35.965452909469604


In [70]:
np.random.seed(95)
trace_points = np.random.choice(range(4096), 10, replace=False)
p_vec = np.arange(4096)
trace_flag = np.isin(p_vec, trace_points)

fig = go.Figure()
fig.add_trace(go.Scatter3d(x=points0[:, 2], y=points0[:, 1], z=-points0[:, 0], mode="markers", marker=dict(opacity=0.2, color=-points0[:, 0])))
fig.add_trace(go.Scatter3d(x=points0[trace_flag, 2], y=points0[trace_flag, 1], z=-points0[trace_flag, 0], mode="markers"))

fig.show()

In [68]:
fig = go.Figure()
fig.add_trace(go.Scatter3d(x=points1[:, 2], y=points1[:, 1], z=-points1[:, 0], mode="markers", marker=dict(opacity=0.05, color=-points1[:, 0])))
fig.add_trace(go.Scatter3d(x=result01[trace_flag, 2], y=result01[trace_flag, 1], z=-result01[trace_flag, 0], mode="markers"))

fig.show()

In [45]:
fig = go.Figure()
fig.add_trace(go.Scatter3d(x=source_pt[:, 2], y=source_pt[:, 1], z=-source_pt[:, 0], mode="markers"))
fig.add_trace(go.Scatter3d(x=target_pt[:, 2], y=target_pt[:, 1], z=-target_pt[:, 0], mode="markers"))

fig.show()

In [47]:
from sklearn.neighbors import KDTree

nn_k = 5
tree = KDTree(source_pt, leaf_size=2)
nearest_dist, nearest_ind = tree.query(source_pt, k=nn_k + 1)

shift_matrix = result - source_pt
shift_matrix_nn = np.zeros_like(shift_matrix)

for ch in range(shift_matrix.shape[1]):
    p_array = shift_matrix[:, ch]
    p_array_nn = p_array[nearest_ind]
    shift_matrix_nn[:, ch] = np.nanmean(p_array_nn, axis=1)

In [52]:
# shift_matrix = result - source_pt
shift_size = np.sqrt(shift_matrix_nn[:, 2]**2 + shift_matrix_nn[:, 1]**2)

fig = px.scatter_3d(x=source_pt[:, 2], y=source_pt[:, 1], z=-source_pt[:, 0], color=shift_size, range_color=(0, 0.1),)
fig.show()

In [54]:
import math

shift_matrix_norm = shift_matrix_nn.copy()
shift_matrix_norm[:, 0] = shift_matrix_norm[:, 0]*0.25
shift_matrix_norm = np.divide(shift_matrix_norm, np.max(np.abs(shift_matrix_norm), axis=1)[:, np.newaxis]) 

fig = go.Figure()

fig.update_layout(scene = dict(
                xaxis_title='UMAP 1',
                yaxis_title='UMAP 2',
                zaxis_title='UMAP 3',
                xaxis = dict(showticklabels=False),
                yaxis = dict(showticklabels=False),
                zaxis = dict(showticklabels=False)))

angle = 0
za = 0.2
vec = np.asarray([math.cos(angle), math.sin(angle), za])
vec = vec*2
camera = dict(
eye=dict(x=vec[0], y=vec[1], z=vec[2]))
    
# lim_scene =  dict(
                # xaxis = dict(nticks=4, range=[-2, 12],),
                # yaxis = dict(nticks=4, range=[-10, 12],),
                # zaxis = dict(nticks=4, range=[-7.5, 10],),)

fig.update_layout(scene_camera=camera, scene_dragmode='orbit')
    #define the trace for triangle sides
cones = go.Cone(
    x=source_pt[:, 2],
    y=source_pt[:, 1],
    z=-source_pt[:, 0],
    u=shift_matrix_norm[:, 2],
    v=shift_matrix_norm[:, 1],
    w=shift_matrix_norm[:, 0],
    colorscale="magma",
    sizemode="absolute",
    sizeref=1.8,
    # anchor="tip",
    showscale=True,
lighting_specular=2)
    
fig.add_trace(cones)
# fig.update_layout(
# autosize=False,
# width=1500,
# height=1500)
# fig.update_layout(scene=lim_scene)



fig.show()